In [1]:
!pip install kaggle-environments -U

Requirement already up-to-date: kaggle-environments in c:\users\julian\anaconda3\lib\site-packages (1.8.12)


In [4]:
from kaggle_environments import make

In [11]:
# this snippet finds all resources stored on the map and puts them into a list so we can search over them
def find_resources(game_state):
    resource_tiles: list[Cell] = []
    width, height = game_state.map_width, game_state.map_height
    for y in range(height):
        for x in range(width):
            cell = game_state.map.get_cell(x, y)
            if cell.has_resource():
                resource_tiles.append(cell)
    return resource_tiles

# the next snippet finds the closest resources that we can mine given position on a map
def find_closest_resources(pos, player, resource_tiles):
    closest_dist = math.inf
    closest_resource_tile = None
    for resource_tile in resource_tiles:
        # we skip over resources that we can't mine due to not having researched them
        if resource_tile.resource.type == Constants.RESOURCE_TYPES.COAL and not player.researched_coal(): continue
        if resource_tile.resource.type == Constants.RESOURCE_TYPES.URANIUM and not player.researched_uranium(): continue
        dist = resource_tile.pos.distance_to(pos)
        if dist < closest_dist:
            closest_dist = dist
            closest_resource_tile = resource_tile
    return closest_resource_tile

In [12]:
# snippet to find the closest city tile to a position
def find_closest_city_tile(pos, player):
    closest_city_tile = None
    if len(player.cities) > 0:
        closest_dist = math.inf
        # the cities are stored as a dictionary mapping city id to the city object, which has a citytiles field that
        # contains the information of all citytiles in that city
        for k, city in player.cities.items():
            for city_tile in city.citytiles:
                dist = city_tile.pos.distance_to(pos)
                if dist < closest_dist:
                    closest_dist = dist
                    closest_city_tile = city_tile
    return closest_city_tile

In [131]:
def random_free(unit, banned, direc):
    d1 = ['n', 's']
    d2 = ['e', 'w']
    if direc in d1:
        d1.remove(direc)
        dirs = d2 + ['c'] + d1
    elif direc in d2:
        d2.remove(direc)
        dirs = d1 + ['c'] + d2
    else:
        dirs = ['n', 's', 'e', 'w']
    
    for direc in dirs:
        new_target = unit.pos.translate(direc, 1)
        if not((new_target.x, new_target.y) in banned) and (new_target.x < game_state.map_width) and (new_target.y < game_state.map_height):
            banned.add((new_target.x, new_target.y))
            return direc
    return 'c'

In [138]:
# for kaggle-environments
from lux.game import Game
from lux.game_map import Cell, RESOURCE_TYPES, Position
from lux.constants import Constants
from lux.game_constants import GAME_CONSTANTS
from lux import annotate
import math
import sys
import random

game_state = None
def agent(observation, configuration):
    global game_state

    ### Do not edit ###
    if observation["step"] == 0:
        game_state = Game()
        game_state._initialize(observation["updates"])
        game_state._update(observation["updates"][2:])
        game_state.id = observation.player
    else:
        game_state._update(observation["updates"])
    
    actions = []

    ### AI Code goes down here! ### 
    player = game_state.players[observation.player]
    opponent = game_state.players[(observation.player + 1) % 2]
    width, height = game_state.map.width, game_state.map.height

    resource_tiles = find_resources(game_state)
    
    # BANNED TILES
    banned = set()
    
    # Fuel only gets used up at night so we need enough to last the nights
    nights_left = 10 * (9 - observation["step"] // 40) # (This wasn't used, but i'm leaving it here)
    new_city = True
    
    for city in player.cities.values():
        req_fuel = min(20, nights_left) * city.get_light_upkeep() # There are 90 nights total

        if city.fuel < req_fuel:
            # let's not build a new one yet
            new_city = False
            
        # Do stuff with our citytiles
        pending = 0
        for tile in city.citytiles:
            if tile.can_act():
                
                # If we have fewer units than cities create a unit
                if len(player.units) + pending < sum([len(city.citytiles) for city in player.cities.values()]):
                    action = tile.build_worker()
                    banned.add((tile.pos.x, tile.pos.y))
                    actions.append(action)
                    pending += 1
                
                # Otherwise do research
                else:
                    action = tile.research()
                    actions.append(action)

###########################################################                    

    # Opponents citytiles are banned
    for city in opponent.cities.values():
        for city_tile in city.citytiles:
            banned.add((city_tile.pos.x, city_tile.pos.y))
    
    for unit in player.units:
        
        # if the unit is a worker (can mine resources) and can perform an action this turn
        if unit.is_worker() and unit.can_act():
            
            # Find the closest city tile and its distance from the unit
            closest_city_tile = find_closest_city_tile(unit.pos, player)
            closest_resource_tile = find_closest_resources(unit.pos, player, resource_tiles)
            
            d_city = unit.pos.distance_to(closest_city_tile.pos)
            d_resource = unit.pos.distance_to(closest_resource_tile.pos) # (This wasn't used, but i'm leaving it here)
            
            
            if observation["step"] % 40 >= 26 or (observation["step"] % 40 >= 30 and 0 < d_city <= 2): #  FIX THIS LATER. Make it go home properly.
                direction = unit.pos.direction_to(closest_city_tile.pos)
                target = unit.pos.translate(direction, 1)
                    
                if (target.x, target.y) in banned:

                    action = unit.move(random_free(unit, banned, direction))
                    actions.append(action)

                else:
                    banned.add((target.x, target.y))
                    action = unit.move(direction)
                    actions.append(action)

                continue
            
            if observation["step"] % 40 >= 30:
                continue
            
            if (unit.can_build(game_state.map) and new_city and (d_city==1)) or closest_city_tile is None:
                action = unit.build_city()
                banned.add((unit.pos.x, unit.pos.y))
                actions.append(action)
                
            
            # we want to mine only if there is space left in the worker's cargo
            elif unit.get_cargo_space_left() > 0:
                # find the closest resource if it exists to this unit
                
                if closest_resource_tile is not None:
                    # create a move action to move this unit in the direction of the closest resource tile and add to our actions list
                    direction = unit.pos.direction_to(closest_resource_tile.pos)
                    target = unit.pos.translate(direction, 1)
                    
                    if (target.x, target.y) in banned:
                        
                        action = unit.move(random_free(unit, banned, direction))
                        actions.append(action)
                        
                    else:
                        banned.add((target.x, target.y))
                        action = unit.move(direction)
                        actions.append(action)
            else:
                # find the closest citytile and move the unit towards it to drop resources to a citytile to fuel the city
                if closest_city_tile is not None:
                    # create a move action to move this unit in the direction of the closest resource tile and add to our actions list
                    direction = unit.pos.direction_to(closest_city_tile.pos)
                    target = unit.pos.translate(direction, 1)
                    
                    if (target.x, target.y) in banned:
                        action = unit.move(random_free(unit, banned, direction))
                        actions.append(action)
                        
                    else:
                        banned.add((target.x, target.y))
                        action = unit.move(direction)
                        actions.append(action)
                    
    
    
    return actions

In [139]:
env = make("lux_ai_2021", configuration={"seed": 51930, "loglevel": 2, "annotations": True}, debug=True)
steps = env.run([agent, "simple_agent"])

[WARN] (match_zuwt2KWlko1K) - turn 103; Unit u_3 collided when trying to move s to (9, 14)
[WARN] (match_zuwt2KWlko1K) - turn 126; Unit u_1 collided when trying to move s to (9, 14)
[WARN] (match_zuwt2KWlko1K) - turn 129; Unit u_4 collided when trying to move e to (10, 14)
[WARN] (match_zuwt2KWlko1K) - turn 137; Unit u_5 collided when trying to move s to (11, 14)
[WARN] (match_zuwt2KWlko1K) - turn 139; Unit u_5 collided when trying to move e to (12, 13)
[WARN] (match_zuwt2KWlko1K) - turn 142; Unit u_1 collided when trying to move s to (11, 14)
[WARN] (match_zuwt2KWlko1K) - turn 142; Unit u_6 collided when trying to move s to (12, 14)
[WARN] (match_zuwt2KWlko1K) - turn 166; Unit u_4 collided when trying to move s to (10, 17)
[WARN] (match_zuwt2KWlko1K) - turn 168; Unit u_2 collided when trying to move n to (10, 17)
[WARN] (match_zuwt2KWlko1K) - turn 175; Unit u_9 collided when trying to move s to (10, 16)
[WARN] (match_zuwt2KWlko1K) - turn 176; Unit u_3 collided when trying to move n to

[WARN] (match_zuwt2KWlko1K) - turn 312; Unit u_4 collided when trying to move n to (13, 10)
[WARN] (match_zuwt2KWlko1K) - turn 313; Unit u_15 collided when trying to move n to (14, 10)
[WARN] (match_zuwt2KWlko1K) - turn 313; Unit u_33 collided when trying to move n to (13, 10)
[WARN] (match_zuwt2KWlko1K) - turn 314; Unit u_33 collided when trying to move n to (13, 10)
[WARN] (match_zuwt2KWlko1K) - turn 314; Unit u_35 collided when trying to move n to (14, 10)
[WARN] (match_zuwt2KWlko1K) - turn 320; Unit u_1 collided when trying to move e to (17, 13)
[WARN] (match_zuwt2KWlko1K) - turn 321; Unit u_1 collided when trying to move e to (17, 13)
[WARN] (match_zuwt2KWlko1K) - turn 321; Unit u_27 collided when trying to move n to (12, 11)
[WARN] (match_zuwt2KWlko1K) - turn 321; Unit u_29 collided when trying to move n to (13, 10)
[WARN] (match_zuwt2KWlko1K) - turn 321; Unit u_31 collided when trying to move e to (10, 14)
[WARN] (match_zuwt2KWlko1K) - turn 321; Unit u_38 collided when trying to

In [140]:
env.render(mode="ipython", width=900, height=600)


In [141]:
%%writefile agent.py
# for kaggle-environments
from lux.game import Game
from lux.game_map import Cell, RESOURCE_TYPES
from lux.constants import Constants
from lux.game_constants import GAME_CONSTANTS
from lux import annotate
import math
import random
import sys

### Define helper functions

# this snippet finds all resources stored on the map and puts them into a list so we can search over them
def find_resources(game_state):
    resource_tiles: list[Cell] = []
    width, height = game_state.map_width, game_state.map_height
    for y in range(height):
        for x in range(width):
            cell = game_state.map.get_cell(x, y)
            if cell.has_resource():
                resource_tiles.append(cell)
    return resource_tiles

# the next snippet finds the closest resources that we can mine given position on a map
def find_closest_resources(pos, player, resource_tiles):
    closest_dist = math.inf
    closest_resource_tile = None
    for resource_tile in resource_tiles:
        # we skip over resources that we can't mine due to not having researched them
        if resource_tile.resource.type == Constants.RESOURCE_TYPES.COAL and not player.researched_coal(): continue
        if resource_tile.resource.type == Constants.RESOURCE_TYPES.URANIUM and not player.researched_uranium(): continue
        dist = resource_tile.pos.distance_to(pos)
        if dist < closest_dist:
            closest_dist = dist
            closest_resource_tile = resource_tile
    return closest_resource_tile

def find_closest_city_tile(pos, player):
    closest_city_tile = None
    if len(player.cities) > 0:
        closest_dist = math.inf
        # the cities are stored as a dictionary mapping city id to the city object, which has a citytiles field that
        # contains the information of all citytiles in that city
        for k, city in player.cities.items():
            for city_tile in city.citytiles:
                dist = city_tile.pos.distance_to(pos)
                if dist < closest_dist:
                    closest_dist = dist
                    closest_city_tile = city_tile
    return closest_city_tile

def random_free(unit, banned, direc):
    """
    Return the direction of a free tile from the unit. Checks perpendicular directions first.
    
    Args:
    unit: Unit
        The unit we are considering
    banned: set 
        Banned tiles, in tuple form
    direc: char
        The direction which the unit planned to move in
    
    """
    d1 = ['n', 's']
    d2 = ['e', 'w']
    if direc in d1:
        d1.remove(direc)
        dirs = d2 + ['c'] + d1
    elif direc in d2:
        d2.remove(direc)
        dirs = d1 + ['c'] + d2
    else:
        dirs = ['n', 's', 'e', 'w']
    
    for direc in dirs:
        new_target = unit.pos.translate(direc, 1)
        if not((new_target.x, new_target.y) in banned) and (new_target.x < game_state.map_width) and (new_target.y < game_state.map_height):
            banned.add((new_target.x, new_target.y))
            return direc
    return 'c'

game_state = None
def agent(observation, configuration):
    global game_state

    ### Do not edit ###
    if observation["step"] == 0:
        game_state = Game()
        game_state._initialize(observation["updates"])
        game_state._update(observation["updates"][2:])
        game_state.id = observation.player
    else:
        game_state._update(observation["updates"])
    
    actions = []

    ### AI Code goes down here! ### 
    player = game_state.players[observation.player]
    opponent = game_state.players[(observation.player + 1) % 2]
    width, height = game_state.map.width, game_state.map.height

    resource_tiles = find_resources(game_state)
    
    # BANNED TILES
    banned = set()
    
    # Fuel only gets used up at night so we need enough to last the nights
    nights_left = 10 * (9 - observation["step"] // 40) # (This wasn't used, but i'm leaving it here)
    new_city = True
    
    for city in player.cities.values():
        req_fuel = min(20, nights_left) * city.get_light_upkeep() # There are 90 nights total

        if city.fuel < req_fuel:
            # let's not build a new one yet
            new_city = False
            
        # Do stuff with our citytiles
        pending = 0
        for tile in city.citytiles:
            if tile.can_act():
                
                # If we have fewer units than cities create a unit
                if len(player.units) + pending < sum([len(city.citytiles) for city in player.cities.values()]):
                    action = tile.build_worker()
                    banned.add((tile.pos.x, tile.pos.y))
                    actions.append(action)
                    pending += 1
                
                # Otherwise do research
                else:
                    action = tile.research()
                    actions.append(action)

###########################################################                    

    # Opponents citytiles are banned
    for city in opponent.cities.values():
        for city_tile in city.citytiles:
            banned.add((city_tile.pos.x, city_tile.pos.y))
    
    for unit in player.units:
        
        # if the unit is a worker (can mine resources) and can perform an action this turn
        if unit.is_worker() and unit.can_act():
            
            # Find the closest city tile and its distance from the unit
            closest_city_tile = find_closest_city_tile(unit.pos, player)
            closest_resource_tile = find_closest_resources(unit.pos, player, resource_tiles)
            
            d_city = unit.pos.distance_to(closest_city_tile.pos)
            d_resource = unit.pos.distance_to(closest_resource_tile.pos) # (This wasn't used, but i'm leaving it here)
            
            
            if observation["step"] % 40 >= 26 or (observation["step"] % 40 >= 30 and 0 < d_city <= 2): #  FIX THIS LATER. Make it go home properly.
                direction = unit.pos.direction_to(closest_city_tile.pos)
                target = unit.pos.translate(direction, 1)
                    
                if (target.x, target.y) in banned:

                    action = unit.move(random_free(unit, banned, direction))
                    actions.append(action)

                else:
                    banned.add((target.x, target.y))
                    action = unit.move(direction)
                    actions.append(action)

                continue
            
            if observation["step"] % 40 >= 30:
                continue
            
            if (unit.can_build(game_state.map) and new_city and (d_city==1)) or closest_city_tile is None:
                action = unit.build_city()
                banned.add((unit.pos.x, unit.pos.y))
                actions.append(action)
                
            
            # we want to mine only if there is space left in the worker's cargo
            elif unit.get_cargo_space_left() > 0:
                # find the closest resource if it exists to this unit
                
                if closest_resource_tile is not None:
                    # create a move action to move this unit in the direction of the closest resource tile and add to our actions list
                    direction = unit.pos.direction_to(closest_resource_tile.pos)
                    target = unit.pos.translate(direction, 1)
                    
                    if (target.x, target.y) in banned:
                        
                        action = unit.move(random_free(unit, banned, direction))
                        actions.append(action)
                        
                    else:
                        banned.add((target.x, target.y))
                        action = unit.move(direction)
                        actions.append(action)
            else:
                # find the closest citytile and move the unit towards it to drop resources to a citytile to fuel the city
                if closest_city_tile is not None:
                    # create a move action to move this unit in the direction of the closest resource tile and add to our actions list
                    direction = unit.pos.direction_to(closest_city_tile.pos)
                    target = unit.pos.translate(direction, 1)
                    
                    if (target.x, target.y) in banned:
                        action = unit.move(random_free(unit, banned, direction))
                        actions.append(action)
                        
                    else:
                        banned.add((target.x, target.y))
                        action = unit.move(direction)
                        actions.append(action)
                    
    
    
    return actions

Overwriting agent.py


## Create a submission
Now we need to create a .tar.gz file with main.py (and agent.py) at the top level. We can then upload this!

In [23]:
!tar -czf submission.tar.gz *

tar: Couldn't open submission.tar.gz: Permission denied
tar: Error exit delayed from previous errors.
